# Data Preparation

project description here

## 1. Import Libraries dan Load Datasets

In [125]:
# import standard libraries
import numpy as np
import pandas as pd
import geopandas as gpd
import math
import time
import glob

import warnings
warnings.filterwarnings("ignore")


# import viz libraries
import plotly.graph_objects as go
import plotly.express as px
import altair as alt

### 1.1 Load PM 2.5 datasets

In [126]:
# load multiple pm25 datasets dan merge menjadi satu dataframe
main_df = pd.concat(map(pd.read_csv, glob.glob("../datasets/pm25/*.csv")))

# display shape
print("dataframe shape: ", main_df.shape)

dataframe shape:  (118182, 14)


In [127]:
# display lima baris pertama
main_df.head(5)

Site          Parameter            Date (LT)  Year  Month  Day  \
0  Jakarta Central  PM2.5 - Principal  2016-01-01 01:00 AM  2016      1    1   
1  Jakarta Central  PM2.5 - Principal  2016-01-01 02:00 AM  2016      1    1   
2  Jakarta Central  PM2.5 - Principal  2016-01-01 03:00 AM  2016      1    1   
3  Jakarta Central  PM2.5 - Principal  2016-01-01 04:00 AM  2016      1    1   
4  Jakarta Central  PM2.5 - Principal  2016-01-01 05:00 AM  2016      1    1   

   Hour  NowCast Conc.  AQI                    AQI Category  Raw Conc.  \
0     1          256.6  307                       Hazardous      412.0   
1     2          203.3  253                  Very Unhealthy      150.0   
2     3          111.1  180                       Unhealthy       19.0   
3     4           60.5  154                       Unhealthy       10.0   
4     5           40.6  114  Unhealthy for Sensitive Groups       21.0   

  Conc. Unit Duration QC Name  
0      UG/M3     1 Hr   Valid  
1      UG/M3     1 Hr   Valid  
2      UG/M3     1 Hr   Valid  
3      UG/M3     1 Hr   Valid  
4      UG/M3     1 Hr   Valid

### 1.2 Load GSOD datasets

In [128]:
# set file path
gsod_file = "../datasets/gsod/GSOD-Jakarta-2016-2022.csv"

In [129]:
## parses_dates kolom Date dan jadikan sebagai index

gsod_jkt = pd.read_csv(gsod_file,
                       parse_dates=["DATE"],
                       index_col=["DATE"])

# display shape
print("dataframe shape: ", gsod_jkt.shape)

dataframe shape:  (2507, 10)


In [130]:
# display lima baris pertama
gsod_jkt.head()

STATION                     NAME  LATITUDE   LONGITUDE  \
DATE                                                                     
2016-01-01  96745099999  JAKARTA OBSERVATORY, ID -6.183333  106.833333   
2016-01-02  96745099999  JAKARTA OBSERVATORY, ID -6.183333  106.833333   
2016-01-03  96745099999  JAKARTA OBSERVATORY, ID -6.183333  106.833333   
2016-01-04  96745099999  JAKARTA OBSERVATORY, ID -6.183333  106.833333   
2016-01-05  96745099999  JAKARTA OBSERVATORY, ID -6.183333  106.833333   

            ELEVATION   GUST  PRCP  TEMP  VISIB  WDSP  
DATE                                                   
2016-01-01        8.0  999.9  0.00  82.6    4.1   3.3  
2016-01-02        8.0  999.9  0.60  81.4    3.9   3.2  
2016-01-03        8.0  999.9  0.00  84.2    4.3   3.6  
2016-01-04        8.0  999.9  0.00  84.5    4.1   3.3  
2016-01-05        8.0  999.9  0.47  83.2    4.0   2.3

## 2. Data Preprocessing (Cleansing, Transforms, Aggregations)

### 2.1 On PM 2.5 Dataset

In [131]:
# display dataframe
main_df.head(2)

Site          Parameter            Date (LT)  Year  Month  Day  \
0  Jakarta Central  PM2.5 - Principal  2016-01-01 01:00 AM  2016      1    1   
1  Jakarta Central  PM2.5 - Principal  2016-01-01 02:00 AM  2016      1    1   

   Hour  NowCast Conc.  AQI    AQI Category  Raw Conc. Conc. Unit Duration  \
0     1          256.6  307       Hazardous      412.0      UG/M3     1 Hr   
1     2          203.3  253  Very Unhealthy      150.0      UG/M3     1 Hr   

  QC Name  
0   Valid  
1   Valid

In [132]:
# remove unnecessary columns dan rename kolom 
main_df = main_df.drop(columns=["Month", "Day", "Hour", "Parameter", "Conc. Unit"], axis=1)
main_df = main_df.rename(columns={"Date (LT)":"Date", "AQI Category":"AQI_Cat", "Raw Conc.":"Raw_Conc", "NowCast Conc.":"NowCast_Conc"})

main_df.head(2)

Site                 Date  Year  NowCast_Conc  AQI  \
0  Jakarta Central  2016-01-01 01:00 AM  2016         256.6  307   
1  Jakarta Central  2016-01-01 02:00 AM  2016         203.3  253   

          AQI_Cat  Raw_Conc Duration QC Name  
0       Hazardous     412.0     1 Hr   Valid  
1  Very Unhealthy     150.0     1 Hr   Valid

In [133]:
# lihat deskriptif statistik dari datafrnae
main_df.describe().T

count         mean         std     min     25%     50%  \
Year          118182.0  2018.919497    1.977150  2016.0  2017.0  2019.0   
NowCast_Conc  118182.0    17.305622  145.347361  -999.0    20.5    33.9   
AQI           118182.0    77.681094  166.666620  -999.0    69.0    97.0   
Raw_Conc      118182.0    36.711851  114.804265  -999.0    20.0    34.0   

                 75%     max  
Year          2021.0  2022.0  
NowCast_Conc    49.6   865.3  
AQI            136.0   741.0  
Raw_Conc        51.0   985.0

Dari menampilkan deskriptif statistik di atas, terlihat anomali berupa nilai -999 di kolom `AQI`, `NowCast_Conc`, dan `Raw_Conc`. Jika merujuk dari deskripsi dataset, nilai -999 merepresentasikan tidak adanya data yang tercatat pada waktu tersebut. Oleh karena itu, perlu dilakukan tindakan lebih lanjut untuk menghandle anomali ini. Nilai -999 akan diubah menjadi `NaN`.

In [134]:
# replace -999.0 into NaN
main_df = main_df.replace({-999.0:np.nan})

In [135]:
main_df["NowCast_Conc"].describe().T

count    115867.000000
mean         37.611209
std          22.333118
min          -9.000000
25%          21.300000
50%          34.500000
75%          50.000000
max         865.300000
Name: NowCast_Conc, dtype: float64

In [136]:
main_df[main_df["NowCast_Conc"]<=0]

Site                 Date  Year  NowCast_Conc  AQI AQI_Cat  \
495   Jakarta Central  2016-01-21 04:00 PM  2016          -1.1  NaN     NaN   
496   Jakarta Central  2016-01-21 05:00 PM  2016          -3.6  NaN     NaN   
497   Jakarta Central  2016-01-21 06:00 PM  2016          -3.8  NaN     NaN   
498   Jakarta Central  2016-01-21 07:00 PM  2016          -3.4  NaN     NaN   
499   Jakarta Central  2016-01-21 08:00 PM  2016          -2.7  NaN     NaN   
...               ...                  ...   ...           ...  ...     ...   
5986    Jakarta South  2020-09-14 04:00 AM  2020           0.0  0.0    Good   
5987    Jakarta South  2020-09-14 05:00 AM  2020           0.0  0.0    Good   
5989    Jakarta South  2020-09-14 07:00 AM  2020           0.0  0.0    Good   
5990    Jakarta South  2020-09-14 08:00 AM  2020           0.0  0.0    Good   
5991    Jakarta South  2020-09-14 09:00 AM  2020           0.0  0.0    Good   

      Raw_Conc Duration QC Name  
495       -5.0     1 Hr   Valid  
496       -6.0     1 Hr   Valid  
497       -4.0     1 Hr   Valid  
498       -3.0     1 Hr   Valid  
499       -2.0     1 Hr   Valid  
...        ...      ...     ...  
5986      -2.0     1 Hr   Valid  
5987       1.0     1 Hr   Valid  
5989      -1.0     1 Hr   Valid  
5990       0.0     1 Hr   Valid  
5991       0.0     1 Hr   Valid  

[348 rows x 9 columns]

Replace negative numbers with 0

In [137]:
main_df["NowCast_Conc"] = main_df["NowCast_Conc"].mask(main_df["NowCast_Conc"] < 0, 0)

main_df[main_df["NowCast_Conc"]<=0]

Site                 Date  Year  NowCast_Conc  AQI AQI_Cat  \
495   Jakarta Central  2016-01-21 04:00 PM  2016           0.0  NaN     NaN   
496   Jakarta Central  2016-01-21 05:00 PM  2016           0.0  NaN     NaN   
497   Jakarta Central  2016-01-21 06:00 PM  2016           0.0  NaN     NaN   
498   Jakarta Central  2016-01-21 07:00 PM  2016           0.0  NaN     NaN   
499   Jakarta Central  2016-01-21 08:00 PM  2016           0.0  NaN     NaN   
...               ...                  ...   ...           ...  ...     ...   
5986    Jakarta South  2020-09-14 04:00 AM  2020           0.0  0.0    Good   
5987    Jakarta South  2020-09-14 05:00 AM  2020           0.0  0.0    Good   
5989    Jakarta South  2020-09-14 07:00 AM  2020           0.0  0.0    Good   
5990    Jakarta South  2020-09-14 08:00 AM  2020           0.0  0.0    Good   
5991    Jakarta South  2020-09-14 09:00 AM  2020           0.0  0.0    Good   

      Raw_Conc Duration QC Name  
495       -5.0     1 Hr   Valid  
496       -6.0     1 Hr   Valid  
497       -4.0     1 Hr   Valid  
498       -3.0     1 Hr   Valid  
499       -2.0     1 Hr   Valid  
...        ...      ...     ...  
5986      -2.0     1 Hr   Valid  
5987       1.0     1 Hr   Valid  
5989      -1.0     1 Hr   Valid  
5990       0.0     1 Hr   Valid  
5991       0.0     1 Hr   Valid  

[348 rows x 9 columns]

In [138]:
# menampilkan proporsi kualitas data
fig = go.Figure(data=[go.Histogram(y=main_df["QC Name"])])
fig.update_layout(autosize=False,width=600,height=400)
fig.update_layout(font_family="Balto", font_size=15, title="Proporsi Data")
fig.update_layout(yaxis={'categoryorder':'total ascending'}, yaxis_title="Quality Check", xaxis_title="Jumlah Observasi")
fig.layout.template = 'simple_white'
fig.show()

Ada berapa banyak total dari records yang `Invalid` dan `Missing`?

In [139]:
# filter
invalid = main_df[(main_df["QC Name"] == "Invalid") | (main_df["QC Name"] == "Missing")]

# print
print("invalid data: ", invalid.shape[0])

invalid data:  2510


In [140]:
# exclude dataframe dari invalid dan missing QC
main_df = main_df[((main_df["QC Name"] == "Invalid") | (main_df["QC Name"] == "Missing"))==False]
main_df.reset_index(drop=True, inplace=True)
main_df.shape

(115672, 9)

In [141]:
# set kolom date menjadi datetimeindex
main_df["Date"] = pd.to_datetime(main_df["Date"])
main_df = main_df.set_index(pd.DatetimeIndex(main_df["Date"]))

main_df.head(3)

Site                Date  Year  NowCast_Conc  \
Date                                                                           
2016-01-01 01:00:00  Jakarta Central 2016-01-01 01:00:00  2016         256.6   
2016-01-01 02:00:00  Jakarta Central 2016-01-01 02:00:00  2016         203.3   
2016-01-01 03:00:00  Jakarta Central 2016-01-01 03:00:00  2016         111.1   

                       AQI         AQI_Cat  Raw_Conc Duration QC Name  
Date                                                                   
2016-01-01 01:00:00  307.0       Hazardous     412.0     1 Hr   Valid  
2016-01-01 02:00:00  253.0  Very Unhealthy     150.0     1 Hr   Valid  
2016-01-01 03:00:00  180.0       Unhealthy      19.0     1 Hr   Valid

Upsampling dataframe menjadi untuk melihat jumlah observasi dalam satu hari. Pisah masing-masing site sehingga tidak double menjadi 48 jam dalam satu hari.

In [142]:
# upsampling site jakarta selatan
south = main_df[main_df["Site"]=="Jakarta South"]
south = south[~south.index.duplicated(keep='first')]
count_obs_a = south[["Raw_Conc"]].resample("D").count()
count_obs_a.columns = ["Total_obsv"]
count_obs_a["Site"] = "Jakarta Selatan" # buat kolom baru

# berapa banyak yg observasinya kurang dari 75% (18 observasi)?
south_count = count_obs_a[count_obs_a["Total_obsv"] < 18]
print("Total hari yang observasinya kurang dari 75% di Jakarta Selatan: ", len(south_count.index))

Total hari yang observasinya kurang dari 75% di Jakarta Selatan:  147


In [143]:
# display lima baris pertama hasil upsampling
count_obs_a.head()

Total_obsv             Site
Date                                   
2016-01-01          23  Jakarta Selatan
2016-01-02          24  Jakarta Selatan
2016-01-03          24  Jakarta Selatan
2016-01-04          22  Jakarta Selatan
2016-01-05          23  Jakarta Selatan

In [144]:
# upsampling site jakarta pusat
central = main_df[main_df["Site"]=="Jakarta Central"]
central = central[~central.index.duplicated(keep='first')]
count_obs_b = central[["Raw_Conc"]].resample("D").count()
count_obs_b.columns = ["Total_obsv"]
count_obs_b["Site"] = "Jakarta Pusat" # buat kolom baru

# berapa banyak yg observasinya kurang dari 75% (18 observasi)?
central_count = count_obs_b[count_obs_b["Total_obsv"] < 18]
print("Total hari yang observasinya kurang dari 75% di Jakarta Pusat: ", len(central_count.index))

Total hari yang observasinya kurang dari 75% di Jakarta Pusat:  106


In [145]:
# display lima baris pertama hasil upsampling
count_obs_b.head()

Total_obsv           Site
Date                                 
2016-01-01          23  Jakarta Pusat
2016-01-02          24  Jakarta Pusat
2016-01-03          24  Jakarta Pusat
2016-01-04          24  Jakarta Pusat
2016-01-05          24  Jakarta Pusat

In [146]:
## concat both dataframe
frames = [count_obs_a, count_obs_b]
daily_obs_count = pd.concat(frames)
daily_obs_count.sort_index(inplace=True)

## buat list supaya bisa mapping value ke daily_avg nanti
total_obsv = daily_obs_count["Total_obsv"].tolist()
site = daily_obs_count["Site"].tolist()

# display concatenated dataframe
daily_obs_count.head()

Total_obsv             Site
Date                                   
2016-01-01          23  Jakarta Selatan
2016-01-01          23    Jakarta Pusat
2016-01-02          24    Jakarta Pusat
2016-01-02          24  Jakarta Selatan
2016-01-03          24  Jakarta Selatan

Upsampling konsentrasi PM 2.5 untuk masing-masing site, ambil rata-ratanya dan fill `NaN` values.

In [147]:
## upsampling jakarta pusat
med_obs_a = main_df.query("Site == 'Jakarta Central'")[["NowCast_Conc"]].resample("D").median().fillna(method='ffill')
med_obs_a.columns = ["PM25_Conc"]

## upsampling jakarta selatan
med_obs_b = main_df.query("Site == 'Jakarta South'")[["NowCast_Conc"]].resample("D").median().fillna(method='ffill')
med_obs_b.columns = ["PM25_Conc"]

# display
med_obs_a.head()

PM25_Conc
Date                 
2016-01-01      22.30
2016-01-02      31.00
2016-01-03      18.65
2016-01-04      42.25
2016-01-05      60.75

In [148]:
# display
med_obs_b.head()

PM25_Conc
Date                 
2016-01-01      31.40
2016-01-02      37.05
2016-01-03      27.40
2016-01-04      52.80
2016-01-05      76.20

In [149]:
# concat dataframe
frames = [med_obs_a, med_obs_b]
daily_avg = pd.concat(frames)
daily_avg.sort_index(inplace=True)
daily_avg["PM25_Conc"] = round(daily_avg["PM25_Conc"],2)
daily_avg.columns = ["pm25_median"]

# buat kolom baru, ambil dari list yg dibuat sebelumnya
daily_avg["total_obsv"] = total_obsv
daily_avg["lokasi"] = site

# rearrange posisi
col_names = ["lokasi", "pm25_median", "total_obsv"]
daily_avg = daily_avg.reindex(columns=col_names)

# buat kolom valid
daily_avg["validasi"] = ["Valid" if value >= 18 else "Invalid" for value in daily_avg["total_obsv"]]

# disply 10 baris
daily_avg.head(10)

lokasi  pm25_median  total_obsv validasi
Date                                                         
2016-01-01  Jakarta Selatan        22.30          23    Valid
2016-01-01    Jakarta Pusat        31.40          23    Valid
2016-01-02    Jakarta Pusat        31.00          24    Valid
2016-01-02  Jakarta Selatan        37.05          24    Valid
2016-01-03  Jakarta Selatan        18.65          24    Valid
2016-01-03    Jakarta Pusat        27.40          24    Valid
2016-01-04  Jakarta Selatan        42.25          22    Valid
2016-01-04    Jakarta Pusat        52.80          24    Valid
2016-01-05    Jakarta Pusat        60.75          24    Valid
2016-01-05  Jakarta Selatan        76.20          23    Valid

In [150]:
# ada null?
daily_avg.isnull().sum()

lokasi         0
pm25_median    0
total_obsv     0
validasi       0
dtype: int64

Ada berapa hari yang observasinya kurang dari 75% (invalid)?

In [151]:
# tampilkan valid-invalid
fig = go.Figure(data=[go.Histogram(y=daily_avg["validasi"])])
fig.update_layout(autosize=False,width=600,height=400)
fig.update_layout(font_family="Balto", font_size=15, title="Proporsi Data")
fig.update_layout(yaxis={'categoryorder':'total ascending'}, yaxis_title="Status observasi", xaxis_title="Jumlah Hari")
fig.layout.template = 'simple_white'
fig.show()

In [152]:
# hitung persentase hari yang invalid
percentage = (253 / 5034) * 100

print("Jumlah hari dengan observasi kurang dari 75% atau kurang dari 18 : {}%".format(percentage))

Jumlah hari dengan observasi kurang dari 75% atau kurang dari 18 : 5.025824394119984%


Hitung AQI dari rata-rata harian PM2.5

![Alt text](../../../../../../C:/Users/PF1ZKYBY/Documents/pacmann-hackathon/figures/AQI-1.png)

![Alt text](../../../../../../C:/Users/PF1ZKYBY/Documents/pacmann-hackathon/figures/AQI.png)

In [153]:
def aqi_equation(x):
        """
        this function will calculate AQI score from given PM2.5 daily average
        """
        if (x > 0) & (x < 12.1):
                calc = ((50 - 0) / (12.0 - 0.0)) * (x - 0.0) + 0
                return round(calc,1)
        elif (x >= 12.1) & (x < 35.5):
                calc = ((100 - 51) / (35.4 - 12.1)) * (x - 12.1) + 51
                return round(calc,1)
        elif (x >= 35.5) & (x < 55.5):
                calc = ((150 - 101) / (55.4 - 35.5)) * (x - 35.5) + 101
                return round(calc,1)
        elif (x >= 55.5) & (x < 150.5):
                calc = ((200 - 151) / (150.4 - 55.5)) * (x - 55.5) + 151
                return round(calc,1)
        elif (x >= 150.5) & (x < 250.5):
                calc = ((300 - 201) / (250.4 - 150.5)) * (x - 150.5) + 201
                return round(calc,1)
        elif (x >= 250.5) & (x < 500.5):
                calc = ((500 - 301) / (500.4 - 250.5)) * (x - 250.5) + 301
                return round(calc,1)
        else:
                return np.nan

In [154]:
def aqi_cat(x):
    """
    this function will return category from given range.
    """
    if (x > 0) & (x <= 51):
        cat = "Baik"
        return cat
    elif (x > 51) & (x <= 101):
        cat = "Sedang"
        return cat
    elif (x > 101) & (x <= 151):
        cat = "Tidak Sehat Untuk Kelompok Rentan"
        return cat
    elif (x > 151) & (x <= 201):
        cat = "Tidak Sehat"
        return cat
    elif (x > 201) & (x <= 301):
        cat = "Sangat Tidak Sehat"
        return cat
    elif (x >= 301) & (x <= 500):
        cat = "Berbahaya"
        return cat
    else:
        return np.nan

In [155]:
# apply function to new columns
daily_avg["aqi"] = daily_avg["pm25_median"].apply(lambda x: aqi_equation(x))
daily_avg["kategori"] = daily_avg["aqi"].apply(lambda x: aqi_cat(x))
daily_avg.head()

lokasi  pm25_median  total_obsv validasi    aqi  \
Date                                                                   
2016-01-01  Jakarta Selatan        22.30          23    Valid   72.5   
2016-01-01    Jakarta Pusat        31.40          23    Valid   91.6   
2016-01-02    Jakarta Pusat        31.00          24    Valid   90.7   
2016-01-02  Jakarta Selatan        37.05          24    Valid  104.8   
2016-01-03  Jakarta Selatan        18.65          24    Valid   64.8   

                                     kategori  
Date                                           
2016-01-01                             Sedang  
2016-01-01                             Sedang  
2016-01-02                             Sedang  
2016-01-02  Tidak Sehat Untuk Kelompok Rentan  
2016-01-03                             Sedang

In [156]:
# tampilkan proporsi dari setiap kategori
fig = go.Figure(data=[go.Histogram(x=daily_avg["kategori"])])
fig.update_layout(autosize=False,width=800,height=500)
fig.update_layout(font_family="Balto", font_size=15, title="Proporsi Kategori AQI")
fig.update_layout(yaxis={'categoryorder':'total ascending'}, yaxis_title="Jumlah Observasi", xaxis_title="Kategori")
fig.layout.template = 'simple_white'
fig.show()

In [157]:
daily_avg["pm25_median"].describe().T

count    5038.000000
mean       36.070951
std        17.062989
min         0.000000
25%        23.100000
50%        35.500000
75%        47.537500
max       175.300000
Name: pm25_median, dtype: float64

In [158]:
daily_avg[daily_avg["pm25_median"]<=0]

lokasi  pm25_median  total_obsv validasi  aqi kategori
Date                                                                       
2017-12-01  Jakarta Selatan          0.0          20    Valid  NaN      NaN
2022-06-30  Jakarta Selatan          0.0          24    Valid  NaN      NaN

### 2.2 On GSOD Dataset

In [159]:
# display dataframe
gsod_jkt.head(2)

STATION                     NAME  LATITUDE   LONGITUDE  \
DATE                                                                     
2016-01-01  96745099999  JAKARTA OBSERVATORY, ID -6.183333  106.833333   
2016-01-02  96745099999  JAKARTA OBSERVATORY, ID -6.183333  106.833333   

            ELEVATION   GUST  PRCP  TEMP  VISIB  WDSP  
DATE                                                   
2016-01-01        8.0  999.9   0.0  82.6    4.1   3.3  
2016-01-02        8.0  999.9   0.6  81.4    3.9   3.2

In [160]:
# remove unneccessary columns
gsod_jkt = gsod_jkt[["PRCP", "TEMP", "VISIB", "WDSP"]]

# rename columns
gsod_jkt = gsod_jkt.rename(columns={ "TEMP":"MeanTemp", "WDSP":"WindSpeed", "PRCP":"Precipitation","VISIB":"Visibility"})

gsod_jkt.head(2)

Precipitation  MeanTemp  Visibility  WindSpeed
DATE                                                      
2016-01-01            0.0      82.6         4.1        3.3
2016-01-02            0.6      81.4         3.9        3.2

In [161]:
# display descriptive statistics
gsod_jkt.describe().T

count       mean        std   min   25%   50%    75%    max
Precipitation  2507.0   5.851604  23.161736   0.0   0.0   0.0   0.16  99.99
MeanTemp       2507.0  83.623215   1.807423  76.7  82.5  83.8  84.90  88.40
Visibility     2507.0   3.983845   0.173269   3.3   3.9   4.0   4.00   4.70
WindSpeed      2507.0   2.772477   1.186564   0.0   2.0   2.6   3.40  15.10

Merujuk dari deskripsi yang disediakan oleh NOAA-NCEI, nilai 99.99 pada dataset merepresentasikan tidak adanya data yang tercatat pada waktu tersebut. Nilai 9.99 akan diubah menjadi `NaN`.

In [162]:
# replace values into NaN
gsod_jkt = gsod_jkt.replace({99.99:np.nan})

print("total baris dengan NaN values: ", gsod_jkt[gsod_jkt.isnull().any(axis=1)].shape[0])

total baris dengan NaN values:  143


In [163]:
# define fungsi
def to_celcius(temp):
    """
    Fungsi ini akan mengkonversi temperature dalam fahrenheit ke dalam celcius.
    Hanya dapat digunakan untuk fahrenheit ke celcius, bukan kelvin ke celcius.
    """
    celcius = round(((temp - 32) * 5 / 9), 2)
    return celcius

In [164]:
# apply function di kolom baru
gsod_jkt['MeanTemp_Celc'] = to_celcius(gsod_jkt["MeanTemp"])
gsod_jkt['Precipitation_mm'] = [round(value * 25.4, 2) for value in gsod_jkt["Precipitation"]] ## ubah curah hujan harian dari inch ke mm

# display
gsod_jkt.head()

Precipitation  MeanTemp  Visibility  WindSpeed  MeanTemp_Celc  \
DATE                                                                        
2016-01-01           0.00      82.6         4.1        3.3          28.11   
2016-01-02           0.60      81.4         3.9        3.2          27.44   
2016-01-03           0.00      84.2         4.3        3.6          29.00   
2016-01-04           0.00      84.5         4.1        3.3          29.17   
2016-01-05           0.47      83.2         4.0        2.3          28.44   

            Precipitation_mm  
DATE                          
2016-01-01              0.00  
2016-01-02             15.24  
2016-01-03              0.00  
2016-01-04              0.00  
2016-01-05             11.94

In [165]:
# display shape
gsod_jkt.shape

(2507, 6)

### 2.3 Merged PM 2.5 Dataset and GSOD Dataset

In [166]:
# copy dataframe
daily_avg_new = daily_avg.copy()
daily_avg_new.index = daily_avg_new.index.date
daily_avg_new.head(2)

lokasi  pm25_median  total_obsv validasi   aqi kategori
2016-01-01  Jakarta Selatan         22.3          23    Valid  72.5   Sedang
2016-01-01    Jakarta Pusat         31.4          23    Valid  91.6   Sedang

In [167]:
daily_avg_new.isnull().sum()

lokasi         0
pm25_median    0
total_obsv     0
validasi       0
aqi            2
kategori       2
dtype: int64

In [168]:
## define a function
def get_gsod(date):

        """
        this function will return a list of daily climates data that match on the datetime index
        """

        result1 = []
        result2 = []
        result3 = []
        result4 = []


        if date in gsod_jkt.index:
                temp = gsod_jkt["MeanTemp_Celc"][date]
                prcp = gsod_jkt["Precipitation_mm"][date]
                visib = gsod_jkt["Visibility"][date]
                wind = gsod_jkt["WindSpeed"][date]
                result1.append(temp)
                result2.append(prcp)
                result3.append(visib)
                result4.append(wind)

        else:
                result1.append(np.nan)
                result2.append(np.nan)
                result3.append(np.nan)
                result4.append(np.nan)


        return result1[0], result2[0], result3[0], result4[0]

In [169]:
## apply fungsi
%time
temps = []
prcps = []
visibs = []
winds = []

counter = 0
for index, values in daily_avg_new.iterrows():
    date = str(daily_avg_new.index[counter])
    result = get_gsod(date)
    temp = result[0]
    prcp = result[1]
    visib = result[2]
    wind = result[3]
    temps.append(temp)
    prcps.append(prcp)
    visibs.append(visib)
    winds.append(wind)
    counter += 1

daily_avg_new["temperatur"] = temps
daily_avg_new["curah_hujan"] = prcps
daily_avg_new["jarak_pandang"] = visibs
daily_avg_new["kecepatan_angin"] = winds

daily_avg_new.head()

CPU times: total: 0 ns
Wall time: 0 ns


lokasi  pm25_median  total_obsv validasi    aqi  \
2016-01-01  Jakarta Selatan        22.30          23    Valid   72.5   
2016-01-01    Jakarta Pusat        31.40          23    Valid   91.6   
2016-01-02    Jakarta Pusat        31.00          24    Valid   90.7   
2016-01-02  Jakarta Selatan        37.05          24    Valid  104.8   
2016-01-03  Jakarta Selatan        18.65          24    Valid   64.8   

                                     kategori  temperatur  curah_hujan  \
2016-01-01                             Sedang       28.11         0.00   
2016-01-01                             Sedang       28.11         0.00   
2016-01-02                             Sedang       27.44        15.24   
2016-01-02  Tidak Sehat Untuk Kelompok Rentan       27.44        15.24   
2016-01-03                             Sedang       29.00         0.00   

            jarak_pandang  kecepatan_angin  
2016-01-01            4.1              3.3  
2016-01-01            4.1              3.3  
2016-01-02            3.9              3.2  
2016-01-02            3.9              3.2  
2016-01-03            4.3              3.6

In [170]:
# display shape
daily_avg_new.shape

(5038, 10)

In [171]:
# replace value di kolom pm25_median menjadi NaN apabila statusnya invalid
daily_avg_new["pm25_median"].mask(daily_avg_new['validasi']=='Invalid', np.nan, inplace=True)

In [172]:
# display NaN values
daily_avg_new.isnull().sum()

lokasi               0
pm25_median        253
total_obsv           0
validasi             0
aqi                  2
kategori             2
temperatur          24
curah_hujan        310
jarak_pandang       24
kecepatan_angin     24
dtype: int64

In [173]:
# display distribusi curah hujan
alt.data_transformers.disable_max_rows()

base = alt.Chart(daily_avg_new)

bar = base.mark_bar().encode(
    x=alt.X('curah_hujan:Q', bin=True, title="Curah Hujan 24 Jam"),
    y=alt.Y('count()', title="Frekuensi")
)

rule = base.mark_rule(color='red').encode(
    x='mean(curah_hujan):Q',
    size=alt.value(5)
)

bar + rule

alt.LayerChart(...)

In [174]:
daily_avg_new["curah_hujan"].describe().T

count    4728.000000
mean        3.990537
std        11.136163
min         0.000000
25%         0.000000
50%         0.000000
75%         2.030000
max       182.120000
Name: curah_hujan, dtype: float64

In [175]:
# display distribusi pm25
alt.data_transformers.disable_max_rows()

base = alt.Chart(daily_avg_new)

bar = base.mark_bar().encode(
    x=alt.X('pm25_median:Q', bin=True, title="Konsentrasi PM 2.5"),
    y=alt.Y('count()', title="Frekuensi")
)

rule = base.mark_rule(color='red').encode(
    x='mean(curah_hujan):Q',
    size=alt.value(5)
)

bar + rule

alt.LayerChart(...)

In [176]:
daily_avg_new["pm25_median"].describe().T

count    4785.000000
mean       36.072581
std        16.666883
min         0.000000
25%        23.350000
50%        35.500000
75%        47.250000
max       101.850000
Name: pm25_median, dtype: float64

Imputasi NaN values di kolom `curah_hujan` dengan median.

In [177]:
daily_avg_new[daily_avg_new["pm25_median"]<=0]

lokasi  pm25_median  total_obsv validasi  aqi kategori  \
2017-12-01  Jakarta Selatan          0.0          20    Valid  NaN      NaN   
2022-06-30  Jakarta Selatan          0.0          24    Valid  NaN      NaN   

            temperatur  curah_hujan  jarak_pandang  kecepatan_angin  
2017-12-01       27.83          NaN            4.0              3.6  
2022-06-30       28.56          0.0            4.0              3.1

In [178]:
daily_avg_new[daily_avg_new["pm25_median"].isnull()]

lokasi  pm25_median  total_obsv validasi    aqi  \
2016-02-14  Jakarta Selatan          NaN          17  Invalid  113.8   
2016-05-13  Jakarta Selatan          NaN          15  Invalid  112.8   
2016-05-25  Jakarta Selatan          NaN          17  Invalid  105.1   
2016-05-26  Jakarta Selatan          NaN          13  Invalid   97.6   
2016-06-05    Jakarta Pusat          NaN          17  Invalid  162.3   
...                     ...          ...         ...      ...    ...   
2022-11-03  Jakarta Selatan          NaN           3  Invalid  147.8   
2022-11-03    Jakarta Pusat          NaN          13  Invalid   95.7   
2022-11-15    Jakarta Pusat          NaN          11  Invalid   78.8   
2022-11-21  Jakarta Selatan          NaN           1  Invalid   50.2   
2022-11-25    Jakarta Pusat          NaN           1  Invalid   71.4   

                                     kategori  temperatur  curah_hujan  \
2016-02-14  Tidak Sehat Untuk Kelompok Rentan       27.33         5.08   
2016-05-13  Tidak Sehat Untuk Kelompok Rentan       30.61        11.94   
2016-05-25  Tidak Sehat Untuk Kelompok Rentan       30.06         0.00   
2016-05-26                             Sedang       29.72         0.00   
2016-06-05                        Tidak Sehat       28.44         0.00   
...                                       ...         ...          ...   
2022-11-03  Tidak Sehat Untuk Kelompok Rentan       29.06         0.00   
2022-11-03                             Sedang       29.06         0.00   
2022-11-15                             Sedang       29.06         0.00   
2022-11-21                               Baik         NaN          NaN   
2022-11-25                             Sedang         NaN          NaN   

            jarak_pandang  kecepatan_angin  
2016-02-14            4.1              2.8  
2016-05-13            4.1              2.5  
2016-05-25            4.2              2.0  
2016-05-26            4.1              2.2  
2016-06-05            4.0              1.6  
...                   ...              ...  
2022-11-03            3.9              1.9  
2022-11-03            3.9              1.9  
2022-11-15            3.9              1.9  
2022-11-21            NaN              NaN  
2022-11-25            NaN              NaN  

[253 rows x 10 columns]

In [179]:
# ubah 0 di kolom pm25_median menjadi NaN, kemudian interpolasi
daily_avg_new["pm25_median"] = daily_avg_new["pm25_median"].mask(daily_avg_new["pm25_median"] <= 0, np.nan)

In [180]:
daily_avg_new.isnull().sum()

lokasi               0
pm25_median        255
total_obsv           0
validasi             0
aqi                  2
kategori             2
temperatur          24
curah_hujan        310
jarak_pandang       24
kecepatan_angin     24
dtype: int64

In [181]:
## fill missing numeric kolom dengan median, terutama di kolom pm25_median dan curah_hujan karena distribusi terlihat skewed
daily_avg_new["pm25_median"] = daily_avg_new["pm25_median"].fillna(daily_avg_new["pm25_median"].median())
daily_avg_new["temperatur"] = daily_avg_new["temperatur"].fillna(daily_avg_new["temperatur"].median())
daily_avg_new["curah_hujan"] = daily_avg_new["curah_hujan"].fillna(daily_avg_new["curah_hujan"].median())
daily_avg_new["jarak_pandang"] = daily_avg_new["jarak_pandang"].fillna(daily_avg_new["jarak_pandang"].median())
daily_avg_new["kecepatan_angin"] = daily_avg_new["kecepatan_angin"].fillna(daily_avg_new["kecepatan_angin"].median())

# daily_avg_new["pm25_median"].interpolate(method='linear', inplace=True)
# daily_avg_new["temperatur"].interpolate(method='linear', inplace=True)
# daily_avg_new["curah_hujan"].interpolate(method='linear', inplace=True)
# daily_avg_new["jarak_pandang"].interpolate(method='linear', inplace=True)
# daily_avg_new["kecepatan_angin"].interpolate(method='linear', inplace=True)



## fill missing categorical columns
from sklearn.impute import SimpleImputer
impCategorical = SimpleImputer(missing_values=np.nan, 
                               strategy='most_frequent')

cats = daily_avg_new[["aqi", "kategori"]]
daily_avg_new[["aqi", "kategori"]] = impCategorical.fit(cats).transform(cats)

In [182]:
daily_avg_new

lokasi  pm25_median  total_obsv validasi    aqi  \
2016-01-01  Jakarta Selatan        22.30          23    Valid   72.5   
2016-01-01    Jakarta Pusat        31.40          23    Valid   91.6   
2016-01-02    Jakarta Pusat        31.00          24    Valid   90.7   
2016-01-02  Jakarta Selatan        37.05          24    Valid  104.8   
2016-01-03  Jakarta Selatan        18.65          24    Valid   64.8   
...                     ...          ...         ...      ...    ...   
2022-11-21  Jakarta Selatan        35.50           1  Invalid   50.2   
2022-11-22    Jakarta Pusat         8.70          24    Valid   36.2   
2022-11-23    Jakarta Pusat        17.25          24    Valid   61.8   
2022-11-24    Jakarta Pusat        13.95          24    Valid   54.9   
2022-11-25    Jakarta Pusat        35.50           1  Invalid   71.4   

                                     kategori  temperatur  curah_hujan  \
2016-01-01                             Sedang       28.11         0.00   
2016-01-01                             Sedang       28.11         0.00   
2016-01-02                             Sedang       27.44        15.24   
2016-01-02  Tidak Sehat Untuk Kelompok Rentan       27.44        15.24   
2016-01-03                             Sedang       29.00         0.00   
...                                       ...         ...          ...   
2022-11-21                               Baik       28.78         0.00   
2022-11-22                               Baik       28.78         0.00   
2022-11-23                             Sedang       28.78         0.00   
2022-11-24                             Sedang       28.78         0.00   
2022-11-25                             Sedang       28.78         0.00   

            jarak_pandang  kecepatan_angin  
2016-01-01            4.1              3.3  
2016-01-01            4.1              3.3  
2016-01-02            3.9              3.2  
2016-01-02            3.9              3.2  
2016-01-03            4.3              3.6  
...                   ...              ...  
2022-11-21            4.0              2.6  
2022-11-22            4.0              2.6  
2022-11-23            4.0              2.6  
2022-11-24            4.0              2.6  
2022-11-25            4.0              2.6  

[5038 rows x 10 columns]

In [183]:
daily_avg_new.isnull().sum()

lokasi             0
pm25_median        0
total_obsv         0
validasi           0
aqi                0
kategori           0
temperatur         0
curah_hujan        0
jarak_pandang      0
kecepatan_angin    0
dtype: int64

In [184]:
# remove unnecessary columns (jumlah observasi dan validasi)
daily_avg_new.drop(['total_obsv', 'validasi'], axis=1, inplace=True)

## 3. Export Preprocessed Dataset

In [185]:
# display dataframe
daily_avg_new

lokasi  pm25_median    aqi  \
2016-01-01  Jakarta Selatan        22.30   72.5   
2016-01-01    Jakarta Pusat        31.40   91.6   
2016-01-02    Jakarta Pusat        31.00   90.7   
2016-01-02  Jakarta Selatan        37.05  104.8   
2016-01-03  Jakarta Selatan        18.65   64.8   
...                     ...          ...    ...   
2022-11-21  Jakarta Selatan        35.50   50.2   
2022-11-22    Jakarta Pusat         8.70   36.2   
2022-11-23    Jakarta Pusat        17.25   61.8   
2022-11-24    Jakarta Pusat        13.95   54.9   
2022-11-25    Jakarta Pusat        35.50   71.4   

                                     kategori  temperatur  curah_hujan  \
2016-01-01                             Sedang       28.11         0.00   
2016-01-01                             Sedang       28.11         0.00   
2016-01-02                             Sedang       27.44        15.24   
2016-01-02  Tidak Sehat Untuk Kelompok Rentan       27.44        15.24   
2016-01-03                             Sedang       29.00         0.00   
...                                       ...         ...          ...   
2022-11-21                               Baik       28.78         0.00   
2022-11-22                               Baik       28.78         0.00   
2022-11-23                             Sedang       28.78         0.00   
2022-11-24                             Sedang       28.78         0.00   
2022-11-25                             Sedang       28.78         0.00   

            jarak_pandang  kecepatan_angin  
2016-01-01            4.1              3.3  
2016-01-01            4.1              3.3  
2016-01-02            3.9              3.2  
2016-01-02            3.9              3.2  
2016-01-03            4.3              3.6  
...                   ...              ...  
2022-11-21            4.0              2.6  
2022-11-22            4.0              2.6  
2022-11-23            4.0              2.6  
2022-11-24            4.0              2.6  
2022-11-25            4.0              2.6  

[5038 rows x 8 columns]

In [186]:
processed_df = daily_avg_new.reset_index()
processed_df = processed_df.rename(columns={"index":"tanggal", "pm25_median":"pm25"})
processed_df

tanggal           lokasi   pm25    aqi  \
0     2016-01-01  Jakarta Selatan  22.30   72.5   
1     2016-01-01    Jakarta Pusat  31.40   91.6   
2     2016-01-02    Jakarta Pusat  31.00   90.7   
3     2016-01-02  Jakarta Selatan  37.05  104.8   
4     2016-01-03  Jakarta Selatan  18.65   64.8   
...          ...              ...    ...    ...   
5033  2022-11-21  Jakarta Selatan  35.50   50.2   
5034  2022-11-22    Jakarta Pusat   8.70   36.2   
5035  2022-11-23    Jakarta Pusat  17.25   61.8   
5036  2022-11-24    Jakarta Pusat  13.95   54.9   
5037  2022-11-25    Jakarta Pusat  35.50   71.4   

                               kategori  temperatur  curah_hujan  \
0                                Sedang       28.11         0.00   
1                                Sedang       28.11         0.00   
2                                Sedang       27.44        15.24   
3     Tidak Sehat Untuk Kelompok Rentan       27.44        15.24   
4                                Sedang       29.00         0.00   
...                                 ...         ...          ...   
5033                               Baik       28.78         0.00   
5034                               Baik       28.78         0.00   
5035                             Sedang       28.78         0.00   
5036                             Sedang       28.78         0.00   
5037                             Sedang       28.78         0.00   

      jarak_pandang  kecepatan_angin  
0               4.1              3.3  
1               4.1              3.3  
2               3.9              3.2  
3               3.9              3.2  
4               4.3              3.6  
...             ...              ...  
5033            4.0              2.6  
5034            4.0              2.6  
5035            4.0              2.6  
5036            4.0              2.6  
5037            4.0              2.6  

[5038 rows x 9 columns]

In [189]:
jakpus = processed_df[processed_df["lokasi"]=="Jakarta Pusat"]
jakpus.head(10)

tanggal         lokasi   pm25    aqi  \
1   2016-01-01  Jakarta Pusat  31.40   91.6   
2   2016-01-02  Jakarta Pusat  31.00   90.7   
5   2016-01-03  Jakarta Pusat  27.40   83.2   
7   2016-01-04  Jakarta Pusat  52.80  143.6   
8   2016-01-05  Jakarta Pusat  60.75  153.7   
10  2016-01-06  Jakarta Pusat  36.10  102.5   
12  2016-01-07  Jakarta Pusat  37.90  106.9   
14  2016-01-08  Jakarta Pusat  28.80   86.1   
16  2016-01-09  Jakarta Pusat  44.90  124.1   
18  2016-01-10  Jakarta Pusat  49.55  135.6   

                             kategori  temperatur  curah_hujan  jarak_pandang  \
1                              Sedang       28.11         0.00            4.1   
2                              Sedang       27.44        15.24            3.9   
5                              Sedang       29.00         0.00            4.3   
7   Tidak Sehat Untuk Kelompok Rentan       29.17         0.00            4.1   
8                         Tidak Sehat       28.44        11.94            4.0   
10  Tidak Sehat Untuk Kelompok Rentan       28.89         0.25            4.3   
12  Tidak Sehat Untuk Kelompok Rentan       30.17         0.00            4.3   
14                             Sedang       29.83         0.00            4.3   
16  Tidak Sehat Untuk Kelompok Rentan       29.28         0.00            4.2   
18  Tidak Sehat Untuk Kelompok Rentan       29.50         0.00            4.2   

    kecepatan_angin  
1               3.3  
2               3.2  
5               3.6  
7               3.3  
8               2.3  
10              2.3  
12              3.9  
14              3.0  
16              4.2  
18              2.7

In [190]:
jakpus.shape

(2521, 9)

In [187]:
# export to csv
processed_df.to_csv("../datasets/processed/daily-pm25-gsod-cleaned.csv", index=False)